In [18]:
# Checks if all the words in a list have odd length and are distinct
def is_odd_and_distinct(fact):
    return all(len(f) % 2 == 1 for f in fact) and len(fact) == len(Set(fact))

# This is the main bijection, called $\Psi$ in the paper
def bijection_odd_distinct_to_even(w):
    fact = list(w.lyndon_factorization())
    if not is_odd_and_distinct(fact):
        raise ValueError("Factors are not odd and distinct")
    out = Word('')
    while len(fact) > 1 or (len(fact) == 1 and len(fact[0])>1): # there is more than one letter left
        last = fact.pop() # remove the last factor
        splittable = false
        if len(last) >= 2:
            r,s = last.standard_factorization()
            if len(fact) == 0 or s.lex_less(fact[-1]): 
                splittable = true # the last factor is splittable
        if splittable:
            if len(r) % 2 == 0:  # if r is even, move it to the output; this is a step of type (P)
                fact.append(s)
                out = r + out
            else: # if s is even, move it to the output; this is a step of type (S)
                fact.append(r)
                out = s + out
        else: # the last factor is not splittable; this is a step of type (F)
            secondtolast = fact.pop()
            out = last + secondtolast + out # switch the last two odd factors and move them to the output
    # now there is either one letter or no letters left
    if len(fact) == 1: # if there is a letter left, move it to the outout to the place where it would go lexicographically
        last = fact.pop()
        evenfact = sorted(out.lyndon_factorization() + [last]) # add it to the list of Lyndon factoris of the output
        out = product(w for w in evenfact[::-1]) # list the factors in decreasing lexicographic order and concatenate them
    return out

# Checks if all the words in a list have even length, except possibly for one word of length one
def is_even_plus_single(fact):
    sum_odd_lengths = 0
    for f in fact:
        if len(f) % 2 == 1:
            sum_odd_lengths += len(f)
    return sum_odd_lengths <= 1

# Computes the iterated standard factorization (ISF) of an Lyndon word l with respect to another word u (which can be Infinity)
def iterated_standard_factorization(l,u):
    r,s = l.standard_factorization()
    while len(s) % 2 == 0 and (u == Infinity or s.lex_less(u)):
        r,s = r.standard_factorization()
    return r,s

# The following is the inverse of the main bijection, called $\Omega$ in the paper
def bijection_even_to_odd_distinct(w):
    fact = list(w.lyndon_factorization())
    if not is_even_plus_single(fact):
        raise ValueError("Factors are not even (plus possibly a single letter)")
    if len(w) % 2 == 1: #case of odd n
        for f in fact:
            if len(f) == 1: # find the factor of length one, remove it from the factorization, and put it in the output
                fact.remove(f)
                out = [f] 
    else:
        out = [] # out will be the Lyndon factorization of the output word
    while len(fact) >= 1:
        first = fact.pop(0) # remove the first factor
        if len(out)>0:
            last = out[-1] # the last factor from the output
        else:
            last = Infinity # a word that is larger than all the others
        if last != Infinity and last.lex_less(first): # this is a step of type (S')
            out = out[:-1] + [last * first] #insert "first" to the right of the last factor of the output
        else:
            r,s = iterated_standard_factorization(first,last)
            first = first[len(r)+len(s):] #remove the prefix rs from "first", factorize what is left, and put it back into fact
            fact = list(first.lyndon_factorization()) + fact 
            if last != Infinity and not s.lex_less(last): 
                # the ISF stopped because the suffix got too big; this is a step of type (P')
                out = out[:-1] + [r * s * last] #insert rs to the left of the last factor of the output
            else:
                #the ISF didn't stop because the suffix got to big, so it was because the suffix was odd; this is a step of type (F')
                out = out + [s,r] #switch r and s and append them to the output
    return product(w for w in out)


In [37]:
# examples
for w in [Word('10010011'),Word('bccbbcbabbaabaaabba'),Word('21122121221222100110011110101011'),Word('2112212122122210011001110101001111'),Word('303233032031')]:
    Phiw = bijection_odd_distinct_to_even(w)
    print("w=\t\t",w)
    print("Phi(w)=\t\t",Phiw)
    print("Om(Phi(w))=\t",bijection_even_to_odd_distinct(Phiw))

for ww in [Word('21222122212112201011101010011110011'),Word('2302120213')]:
    Omegaww = bijection_even_to_odd_distinct(ww)
    print("w'=\t\t",ww)
    print("Om(w')=\t\t",Omegaww)
    print("Phi(Om(w'))=\t",bijection_odd_distinct_to_even(Omegaww))


w=		 10010011
Phi(w)=		 01010011
Om(Phi(w))=	 10010011
w=		 bccbbcbabbaabaaabba
Phi(w)=		 cbcbbbcaabbabaaaabb
Om(Phi(w))=	 bccbbcbabbaabaaabba
w=		 21122121221222100110011110101011
Phi(w)=		 12221222121122011101010011110011
Om(Phi(w))=	 21122121221222100110011110101011
w=		 2112212122122210011001110101001111
Phi(w)=		 1222122212112201011101010011110011
Om(Phi(w))=	 2112212122122210011001110101001111
w=		 303233032031
Phi(w)=		 233303031032
Om(Phi(w))=	 303233032031
w'=		 21222122212112201011101010011110011
Om(w')=		 11221212221222210011001110101001111
Phi(Om(w'))=	 21222122212112201011101010011110011
w'=		 2302120213
Om(w')=		 3021302212
Phi(Om(w'))=	 2302120213


In [38]:
# The following is an alternative description of $\Omega$, which does not use require computing the iterated standard factorization.
# This description is simpler, but proving that it is the inverse of $\Psi$ is harder, which is why this version is not used in the paper
def bijection_even_to_odd_distinct_noISF(w):
    fact = list(w.lyndon_factorization())
    if not is_even_plus_single(fact):
        raise ValueError("Factors are not even (plus possibly a single letter)")
    if len(w) % 2 == 1: # case of odd n
        for f in fact:
            if len(f) == 1: # find the factor of length one, remove it from the factorization, and put it in the output
                fact.remove(f)
                out = [f] 
    else:
        out = [] # out will be the Lyndon factorization of the output word
    while len(fact) >= 1:
        first = fact.pop(0) # remove the first factor
        r,s = first.standard_factorization()
        if len(out) == 0  or s.lex_less(out[-1]): # if the last factor of the output (assuming there is one) is larger than s 
            if len(r) % 2 == 0:  # if r is even, put r and s back as seprate "factors" and repeat
                fact = [r,s] + fact
            else: 
                out = out + [s,r] # switch r and s and append them to the output
        else:
            if first.lex_less(out[-1]): #if "first" is less than the last factor from the output
                out = out[:-1] + [first * out[-1]] # insert "first" to the left of the last factor of the output, as part of the same factor
            else: # if "first" is larger than the last factor from the output
                out = out[:-1] + [out[-1] * first] # insert "first" to the right of the last factor of the output, as part of the same factor
    return product(w for w in out)
    

In [39]:
# examples
for w in [Word('10010011'),Word('bccbbcbabbaabaaabba'),Word('21122121221222100110011110101011'),Word('2112212122122210011001110101001111'),Word('303233032031')]:
    Phiw = bijection_odd_distinct_to_even(w)
    print("w=\t\t",w)
    print("Phi(w)=\t\t",Phiw)
    print("Om(Phi(w))=\t",bijection_even_to_odd_distinct_noISF(Phiw))

for ww in [Word('21222122212112201011101010011110011'),Word('2302120213')]:
    Omegaww = bijection_even_to_odd_distinct_noISF(ww)
    print("w'=\t\t",ww)
    print("Om(w')=\t\t",Omegaww)
    print("Phi(Om(w'))=\t",bijection_odd_distinct_to_even(Omegaww))

w=		 10010011
Phi(w)=		 01010011
Om(Phi(w))=	 10010011
w=		 bccbbcbabbaabaaabba
Phi(w)=		 cbcbbbcaabbabaaaabb
Om(Phi(w))=	 bccbbcbabbaabaaabba
w=		 21122121221222100110011110101011
Phi(w)=		 12221222121122011101010011110011
Om(Phi(w))=	 21122121221222100110011110101011
w=		 2112212122122210011001110101001111
Phi(w)=		 1222122212112201011101010011110011
Om(Phi(w))=	 2112212122122210011001110101001111
w=		 303233032031
Phi(w)=		 233303031032
Om(Phi(w))=	 303233032031
w'=		 21222122212112201011101010011110011
Om(w')=		 11221212221222210011001110101001111
Phi(Om(w'))=	 21222122212112201011101010011110011
w'=		 2302120213
Om(w')=		 3021302212
Phi(Om(w'))=	 2302120213


In [44]:
# Let us now check that Phi is a bijection on words with a given weight, for some small weights.
# First define  the set of words with weight given by a composition
def words_with_given_weight(comp):
    multiset = []
    for i in range(len(comp)):
        for m in range(comp[i]):
            multiset.append(i)
    return [Word(p) for p in Permutations(multiset).list()]
    
# The following function returns two lists of words with weight determined by the a composition:
# the list of words whose Lyndon factors are odd and distinct,
# the list of words whose Lyndon factors are even, except possibly a factor of length 1
def odd_distinct_and_even_words_with_given_weight(comp):
    odd_distinct = []
    even = []
    for w in words_with_given_weight(comp):
        fact = w.lyndon_factorization()
        if is_even_plus_single(fact):
            even.append(w)
        if is_odd_and_distinct(fact):
            odd_distinct.append(w)
    if len(odd_distinct) != len(even):
        raise ValueError("Not the same number of words in both sets!")
    return odd_distinct,even;

print(odd_distinct_and_even_words_with_given_weight([2,2,1]))

([word: 00112, word: 00121, word: 00211, word: 01012, word: 01021, word: 01102, word: 10120, word: 10210, word: 20110, word: 21001], [word: 01120, word: 01210, word: 02110, word: 10012, word: 10021, word: 10102, word: 10201, word: 12010, word: 20011, word: 20101])


In [49]:
# The following function checks that Phi and Omega are inverses of each other on words with weight given by the composition comp
def check_bijection_and_inverse(comp):
    odd_distinct,even = odd_distinct_and_even_words_with_given_weight(comp)
    for w in odd_distinct:
        ww = bijection_odd_distinct_to_even(w)
        www = bijection_even_to_odd_distinct(ww)
        if w != www:
            print(w,ww,www)
            raise ValueError("Omega composed with Phi is not the identity!")
    for w in even:
        ww = bijection_even_to_odd_distinct(w)
        www = bijection_odd_distinct_to_even(ww)
        if w != www:
            print(w,ww,www)
            raise ValueError("Phi composed with Omega is not the identity!")

In [55]:
for i in range(1,14):
    check_bijection_and_inverse([i,13-i])

In [54]:
for n in range(1,9):
    for comp in Compositions(n):
        check_bijection_and_inverse(comp)